### Benchmarking 1

In [1]:
import json
from collections import Counter, defaultdict
from copy import deepcopy
from dataclasses import dataclass, field
from itertools import product
from typing import Optional

import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from qibo import Circuit, gates
from qibo.backends import NumpyBackend, construct_backend
from qibo.quantum_info import fidelity, partial_trace
from qibo.result import QuantumState
from qibo.quantum_info import trace_distance

from qibocal.auto.operation import (
    DATAFILE,
    Data,
    QubitId,
    QubitPairId,
    Results,
    Routine,
)
from qibocal.auto.transpile import dummy_transpiler, execute_transpiled_circuit
from qibocal.calibration import CalibrationPlatform

from qibocal.protocols.state_tomography import StateTomographyParameters, plot_reconstruction
from qibocal.protocols.utils import table_dict, table_html
from sympy import Matrix
from IPython.display import display



/home/lauramartinez/envs/test_env/lib/python3.12/site-packages/cma/s.py:13: UserWarning: Could not import matplotlib.pyplot, therefore ``cma.plot()`` etc. is not available
  _warnings.warn('Could not import matplotlib.pyplot, therefore'


In [2]:
SINGLE_QUBIT_BASIS = ["X", "Y", "Z"]
TWO_QUBIT_BASIS = list(product(SINGLE_QUBIT_BASIS, SINGLE_QUBIT_BASIS))
OUTCOMES = ["00", "01", "10", "11"]
SIMULATED_DENSITY_MATRIX = "ideal"
"""Filename for simulated density matrix."""


TomographyType = np.dtype(
    [("frequencies", np.int64), ("simulation_probabilities", np.float64)]
)
"""Custom dtype for tomography."""


@dataclass
class StateTomographyData(Data):
    """Tomography data."""

    data: dict[tuple[QubitId, QubitId, str, str], np.int64] = field(
        default_factory=dict
    )
    ideal: dict[QubitPairId, np.ndarray] = field(default_factory=dict)
    simulated: Optional[QuantumState] = None

    def save(self, path):
        self._to_npz(path, DATAFILE)
        np.savez(
            path / f"{SIMULATED_DENSITY_MATRIX}.npz",
            **{json.dumps(pair): rho for pair, rho in self.ideal.items()},
        )
        self.simulated.dump(path / "simulated.json")

    @classmethod
    def load(cls, path):
        return cls(
            data=super().load_data(path, DATAFILE),
            ideal=super().load_data(path, SIMULATED_DENSITY_MATRIX),
            simulated=QuantumState.load(path / "simulated.json"),
        )


@dataclass
class StateTomographyResults(Results):
    """Tomography results."""

    measured_raw_density_matrix_real: dict[QubitPairId, list] = field(
        default_factory=dict
    )
    """Real part of measured density matrix before projecting."""
    measured_raw_density_matrix_imag: dict[QubitPairId, list] = field(
        default_factory=dict
    )
    """Imaginary part of measured density matrix before projecting."""

    measured_density_matrix_real: dict[QubitPairId, list] = field(default_factory=dict)
    """Real part of measured density matrix after projecting."""
    measured_density_matrix_imag: dict[QubitPairId, list] = field(default_factory=dict)
    """Imaginary part of measured density matrix after projecting."""

    fidelity: dict[QubitId, float] = field(default_factory=dict)
    """State fidelity."""


def _acquisition(
    initial_state,
    nshots,
    targets: list[QubitPairId],
) -> StateTomographyData:
    """Acquisition protocol for two qubit state tomography experiment."""
    qubits = [q for pair in targets for q in pair]
    for q, counts in Counter(qubits).items():
        if counts > 1:
            raise ValueError(
                f"Qubits can only be measured once, but qubit {q} is measured {counts} times."
            )


    simulator = NumpyBackend()
    # transpiler = dummy_transpiler(backend)
    circuit = Circuit(2)


    simulated_state = simulator.execute_circuit(deepcopy(circuit), initial_state=initial_state)
    data = StateTomographyData(simulated=simulated_state)
    for basis1, basis2 in TWO_QUBIT_BASIS:
        basis_circuit = deepcopy(circuit)
        # FIXME: https://github.com/qiboteam/qibo/issues/1318
        if basis1 != "Z":
            basis_circuit.add(
                getattr(gates, basis1)(2 * i).basis_rotation()
                for i in range(len(targets))
            )
        if basis2 != "Z":
            basis_circuit.add(
                getattr(gates, basis2)(2 * i + 1).basis_rotation()
                for i in range(len(targets))
            )

        basis_circuit.add(
            gates.M(2 * i, 2 * i + 1, register_name=f"reg{i}")
            for i in range(len(targets))
        )

        simulation_result = simulator.execute_circuit(basis_circuit, initial_state=initial_state)
        
        results = simulator.execute_circuit(basis_circuit, nshots=nshots, initial_state=initial_state)

        for i, pair in enumerate(targets):
            frequencies = results.frequencies(registers=True)[f"reg{i}"]
            print(frequencies)
            simulation_probabilities = simulation_result.probabilities(
                qubits=(2 * i, 2 * i + 1)
            )
            data.register_qubit(
                TomographyType,
                pair + (basis1, basis2),
                {
                    "frequencies": np.array([frequencies[i] for i in OUTCOMES]),
                    "simulation_probabilities": simulation_probabilities,
                },
            )
            if basis1 == "Z" and basis2 == "Z":
                nqubits = basis_circuit.nqubits
                traced_qubits = tuple(
                    q for q in range(nqubits) if q not in (2 * i, 2 * i + 1)
                )
                data.ideal[pair] = partial_trace(
                    simulation_result.state(), traced_qubits
                )

    return data


def rotation_matrix(basis):
    """Matrix of the gate implementing the rotation to the given basis.

    Args:
        basis (str): One of Pauli basis: X, Y or Z.
    """
    backend = NumpyBackend()
    if basis == "Z":
        return np.eye(2, dtype=complex)
    return getattr(gates, basis)(0).basis_rotation().matrix(backend)


def project_psd(matrix):
    """Project matrix to the space of positive semidefinite matrices."""
    s, v = np.linalg.eigh(matrix)
    s = s * (s > 0)
    return v.dot(np.diag(s)).dot(v.conj().T)


def _fit(data: StateTomographyData) -> StateTomographyResults:
    """Post-processing for two qubit state tomography.

    Uses a linear inversion algorithm to reconstruct the density matrix
    from measurements, with the following steps:
    1. Construct a linear transformation M, from density matrix
    to Born-probabilities in the space of all two-qubit measurement bases
    (in our case XX, XY, XZ, YX, YY, YZ, ZX, ZY, ZZ).
    2. Invert M to get the transformation from Born-probabilities to
    density matrices.
    3. Calculate vector of Born-probabilities from experimental measurements (frequencies).
    4. Map this vector to a density matrix (``measured_raw_density_matrix``) using the
    inverse of M from step 2.
    5. Project the calculated density matrix to the space of positive semidefinite
    matrices (``measured_density_matrix``) using the function ``project_psd``.
    """
    rotations = [
        np.kron(rotation_matrix(basis1), rotation_matrix(basis2))
        for basis1, basis2 in TWO_QUBIT_BASIS
    ]

    # construct the linear transformation from density matrix to Born-probabilities
    measurement = np.zeros((0, 16))
    for rotation in rotations:
        channel = np.kron(rotation, np.conj(rotation))
        measure_channel = channel[np.eye(4, dtype=bool).flatten(), :]
        measurement = np.concatenate((measurement, measure_channel))
   
    # invert to get linear transformation from Born-probabilities to density matrix
    inverse_measurement = np.linalg.pinv(measurement)

    # Sanity check for the pseudoinverse:
    identity_check = inverse_measurement @ measurement 

    # calculate Born-probabilities vector from measurements (frequencies)
    probabilities = defaultdict(lambda: np.empty(measurement.shape[0]))
    for (qubit1, qubit2, basis1, basis2), value in data.data.items():
        frequencies = value["frequencies"]
        ib = TWO_QUBIT_BASIS.index((basis1, basis2))
        probabilities[(qubit1, qubit2)][4 * ib : 4 * (ib + 1)] = frequencies / np.sum(
            frequencies
        )

    # reconstruction
    results = StateTomographyResults()
    for pair, probs in probabilities.items():
        measured_rho = inverse_measurement.dot(probs).reshape((4, 4))
        measured_rho_proj = project_psd(measured_rho)

        results.measured_raw_density_matrix_real[pair] = measured_rho.real.tolist()
        results.measured_raw_density_matrix_imag[pair] = measured_rho.imag.tolist()
        results.measured_density_matrix_real[pair] = measured_rho_proj.real.tolist()
        results.measured_density_matrix_imag[pair] = measured_rho_proj.imag.tolist()
        results.fidelity[pair] = fidelity(measured_rho_proj, data.ideal[pair])

    return results, measured_rho_proj, identity_check

$\textbf{Testing the code for an specific case}$

In [3]:
#Inputs:
from qibo.quantum_info import random_statevector

initial_state = random_statevector(4) #np.array([1,0,0,0])
nshots = 1000
targets = [(0, 1)]
print(initial_state)
# result_acquisition = _acquisition(initial_state, nshots, targets)

# ideal_rho = result_acquisition.ideal[(0,1)]



[Qibo 0.2.16|INFO|2025-04-21 14:26:41]: Using numpy backend on /CPU:0


[-0.03606288+0.49933196j  0.32906998-0.09667538j  0.66498538-0.35349018j
 -0.0297344 -0.25236657j]


In [4]:
# Linear inversion algorithm for the reconstruction of the density matrix
def linear_inversion_tomography(initial_state, nshots, targets):
    result_acquisition = _acquisition(initial_state, nshots, targets)
    ideal_rho = result_acquisition.ideal[(0,1)]
    results, measured_rho_proj, identity_check = _fit(result_acquisition)
    fidelity_value = results.fidelity[(0, 1)]
    return identity_check, fidelity_value, ideal_rho, measured_rho_proj
   

In [5]:
identity_check, fidelity_value, ideal_rho, measured_rho = linear_inversion_tomography(initial_state, nshots, targets)
print("Identity check:")
display(Matrix(identity_check))
print("Fidelity value:", fidelity_value)

Counter({'11': 385, '10': 289, '00': 236, '01': 90})
Counter({'11': 551, '01': 290, '10': 131, '00': 28})
Counter({'10': 643, '00': 172, '01': 117, '11': 68})
Counter({'11': 455, '10': 445, '01': 63, '00': 37})
Counter({'11': 803, '10': 101, '00': 73, '01': 23})
Counter({'10': 756, '11': 173, '00': 68, '01': 3})
Counter({'10': 382, '01': 262, '11': 228, '00': 128})
Counter({'11': 519, '01': 330, '10': 131, '00': 20})
Counter({'10': 544, '00': 261, '01': 115, '11': 80})
Identity check:


Matrix([
[                  1.0 + 1.07852076885685e-32*I, -1.04544291754626e-16 - 5.71301432595776e-19*I,   3.9331972785613e-17 + 1.07391813113556e-17*I,  2.24389583141099e-17 - 2.57752287692384e-19*I, -6.47801070788975e-18 - 1.44490892404102e-17*I,  5.55111512312578e-17 + 3.09779926500038e-18*I,  2.47963632396743e-17 - 4.35819566249702e-18*I,  3.33465332337348e-17 + 6.64214300539992e-19*I,  9.94459052925316e-17 - 1.70163943042733e-17*I,  1.16328297558387e-17 - 1.30318130423811e-17*I, -8.32667268468867e-17 + 1.15326797524972e-18*I, -3.53883826148238e-17 - 1.15330533472226e-17*I,  1.39902346814031e-17 + 8.41586509219165e-18*I,  7.07368753248736e-17 - 6.27467960336724e-18*I, -6.24498080861957e-18 - 1.15330533472226e-17*I, -8.32667268468867e-17 + 3.16123338050161e-18*I],
[-8.26122531122366e-17 + 2.85555686711526e-18*I,                   1.0 + 1.69243959124987e-16*I, -2.00252141258073e-16 + 1.64798730217797e-17*I,  1.50053580671994e-16 - 4.85722573273506e-17*I,  8.88178419700125e-16 - 2.87

Fidelity value: 1.0123885328551743


In [6]:
display(Matrix(measured_rho)) # Result from linear inversion


Matrix([
[                        0.275841709056406, -0.0685413137086447 + 0.152920807075793*I,   -0.219921752025663 + 0.325178370945465*I,   -0.131442701467079 - 0.0337429194991223*I],
[-0.0685413137086447 - 0.152920807075793*I,                         0.116870460759629,   0.242787531921283 + 0.0390425920891376*I,   0.0298940071121218 + 0.0795456073112531*I],
[ -0.219921752025663 - 0.325178370945465*I,  0.242787531921283 - 0.0390425920891376*I, 0.563074823727715 - 5.55111512312578e-17*I,    0.0735803231407689 + 0.183160180400849*I],
[-0.131442701467079 + 0.0337429194991223*I, 0.0298940071121218 - 0.0795456073112531*I,   0.0735803231407689 - 0.183160180400849*I, 0.0838222990478299 - 1.73472347597681e-18*I]])

In [7]:
display(Matrix(ideal_rho))

Matrix([
[                          0.2506329363022, -0.0601403185158507 + 0.160828763086237*I, -0.200490230071191 + 0.319300580222761*I, -0.124942386080597 - 0.0239484001886686*I],
[-0.0601403185158507 - 0.160828763086237*I,                         0.117633178551953, 0.253000521804066 + 0.0520352883732997*I, 0.0146129370258172 + 0.0859208456134901*I],
[ -0.200490230071191 - 0.319300580222761*I,  0.253000521804066 - 0.0520352883732997*I,                        0.567160864736448,  0.0694361639457872 + 0.178330898137515*I],
[-0.124942386080597 + 0.0239484001886686*I, 0.0146129370258172 - 0.0859208456134901*I, 0.0694361639457872 - 0.178330898137515*I,                        0.0645730204093989]])

$\textbf{Testing the code for 10000 random initial states}$

OBS: What we call initial state is a state has been already prepared with a certain circuit that has led to this state that we call initial state.

In [8]:
iter = 10000
identity_check_list = []
fidelity_list = []
trace_distance_list = []
# Run the linear inversion tomography multiple times
for _ in range(iter):
    initial_state = random_statevector(4)
    identity_check, fidelity_value, ideal_rho, measured_rho = linear_inversion_tomography(initial_state, nshots, targets)
    identity_check_list.append(identity_check)
    fidelity_list.append(fidelity_value)
    trace_distance_value = trace_distance(ideal_rho, measured_rho)
    trace_distance_list.append(trace_distance_value) # Figure of merit

Counter({'01': 522, '11': 342, '00': 80, '10': 56})
Counter({'00': 507, '11': 277, '10': 113, '01': 103})
Counter({'01': 355, '11': 311, '00': 222, '10': 112})
Counter({'11': 781, '00': 141, '01': 60, '10': 18})
Counter({'10': 444, '11': 341, '00': 171, '01': 44})
Counter({'11': 506, '10': 313, '01': 161, '00': 20})
Counter({'11': 674, '01': 209, '10': 92, '00': 25})
Counter({'10': 478, '11': 273, '01': 135, '00': 114})
Counter({'11': 618, '00': 182, '10': 154, '01': 46})
Counter({'00': 721, '11': 139, '10': 79, '01': 61})
Counter({'00': 498, '01': 266, '10': 188, '11': 48})
Counter({'00': 532, '01': 247, '10': 185, '11': 36})
Counter({'00': 567, '10': 225, '01': 185, '11': 23})
Counter({'00': 513, '01': 241, '10': 182, '11': 64})
Counter({'00': 646, '11': 183, '01': 100, '10': 71})
Counter({'00': 552, '10': 262, '01': 147, '11': 39})
Counter({'00': 590, '11': 215, '01': 102, '10': 93})
Counter({'00': 519, '10': 236, '01': 187, '11': 58})
Counter({'10': 408, '00': 308, '11': 176, '01':

In [9]:
print(fidelity_list)

[0.9983849050104733, 0.9850236870612259, 0.9946057558423849, 0.9895979413571052, 1.0190790743705593, 1.021749008934707, 1.000783006798435, 1.0089462240755975, 0.9947816294433914, 0.9870116280019935, 1.004398258572962, 1.011399521555689, 0.9892826614838284, 1.0020456118539511, 1.017659874061713, 1.0017727152575748, 1.0071015656162923, 1.028306746751916, 0.996431860081419, 1.0039088021956237, 0.9981750983835941, 1.0032890663083296, 1.0021696764243064, 1.0006394747646317, 0.9858255279363787, 0.9941934052879479, 0.9982502946601663, 1.0025183471542338, 1.0004509519070297, 0.9877233301446644, 1.0041150308387898, 0.9992390615099158, 0.9973828406849646, 0.9999712725318616, 0.9921237627947523, 0.9861391949101204, 1.0096565673922957, 1.015259443810596, 0.9984990789352016, 0.9953998742208471, 0.9899842155237987, 0.9776251603439738, 0.9943304822122377, 0.99489604430969, 1.0002684718749537, 0.9995574709463892, 1.011623419556015, 0.9853852031466579, 0.9997661061209169, 1.0055573143036036, 0.96946825

In [10]:
print(trace_distance_list)

[0.03520190093621167, 0.04431156386920842, 0.03629198936839186, 0.031041726182172248, 0.032412015356772954, 0.028967816178474267, 0.033175300710829275, 0.03682371321054585, 0.043794907327635815, 0.032492883364363845, 0.021323694323132372, 0.019451597624282835, 0.0269833157382273, 0.035865106942366665, 0.024744368138048572, 0.03999068876419426, 0.022758903612408312, 0.03153704857597981, 0.027537353937145025, 0.03927700492469875, 0.02733461688816855, 0.036387550727652526, 0.018262727659935543, 0.03817702584139905, 0.03318084114152673, 0.03313478382738588, 0.03209361693488925, 0.025216011654019516, 0.030362431348216937, 0.029772076305182422, 0.021941864638504883, 0.022881661094683155, 0.024775962496649914, 0.03502673326691728, 0.027964692145802987, 0.04191248601888009, 0.027525971648456507, 0.040362383934853585, 0.023645452904034123, 0.016145778650155033, 0.030570603879430225, 0.04985136602570708, 0.03496189389773294, 0.03067500139307657, 0.016811735504525607, 0.023289155582131342, 0.0326

In [32]:
# If the difference between each element in the list and 1 is less than 0.1, the result is considered correct. Return True:
"""
Note: The threshold value depends on the number of shots (nshots).
If the number of shots is changed, this value must be adjusted accordingly.
Ensure the threshold is low enough to consider the result acceptable.
"""
def check_fidelity(fidelity_list):
    for fidelity in fidelity_list:
        if abs(fidelity - 1) > 0.05:
            return False
    return True

In [33]:
check_fidelity(fidelity_list)

True

In [34]:
def check_trace_distance(trace_distance_list):
    for trace_distance in trace_distance_list:
        if trace_distance > 0.08:
            return False
    return True


In [35]:
check_trace_distance(trace_distance_list)

True

Since the value is zero up to statistical error, the matrices are equal.

### Benchmarking 2

$$|\psi\rangle = \alpha |00\rangle + \beta |01\rangle + \gamma |10\rangle + \delta |11\rangle$$

$$\rho = |\psi\rangle\langle\psi|$$

$$
\rho = \frac{1}{4} \sum_{i,j=0}^3 \langle \sigma_i \otimes \sigma_j \rangle \, \sigma_i \otimes \sigma_j
$$

where $\langle \sigma_i \otimes \sigma_j \rangle = \mathrm{Tr}(\rho \, \sigma_i \otimes \sigma_j)$ are the expectation values of the $\sigma_i \otimes \sigma_j$ operator.


In [15]:
import numpy as np
from sympy import symbols, Matrix

def define_two_qubit_state(alpha, beta, gamma, delta):
    """
    Defines the state of a two-qubit system in ket (column) and bra (row) form.

    Args:
        alpha, beta, gamma, delta: Symbolic or complex coefficients that define the quantum state.

    Returns:
        ket: Column vector (ket) of the state.
        bra: Row vector (bra) of the state (conjugate of the ket).
    """
    # Define the state in ket form (column vector)
    ket = Matrix([[alpha], [beta], [gamma], [delta]])
    
    # Define the state in bra form (row vector, conjugate of the ket)
    bra = ket.H  # .H returns the conjugate transpose in sympy
    
    return ket, bra

# Define symbolic coefficients
a, b, c, d = symbols('a b c d')

# Use the symbolic coefficients as an example
ket, bra = define_two_qubit_state(a, b, c, d)

print("State in ket form (column):")
print(ket)
print(ket.shape)
print("\nState in bra form (row):")
print(bra)
print(bra.shape)

State in ket form (column):
Matrix([[a], [b], [c], [d]])
(4, 1)

State in bra form (row):
Matrix([[conjugate(a), conjugate(b), conjugate(c), conjugate(d)]])
(1, 4)


Two-qubit bases:

In [16]:
from sympy import Matrix, eye, I, init_printing
from sympy.physics.quantum import TensorProduct
from IPython.display import display

# Initialize pretty printing for better visualization in Jupyter
init_printing()

# Define Pauli matrices
X = Matrix([[0, 1], [1, 0]])  # Pauli-X
Y = Matrix([[0, -I], [I, 0]])  # Pauli-Y
Z = Matrix([[1, 0], [0, -1]])  # Pauli-Z

# Define the measurement bases for a single qubit
basis_map = {
    'I': eye(2), 
    'X': X,
    'Y': Y,
    'Z': Z
}

# Function to calculate the measurement basis matrix for two qubits
def two_qubit_measurement_basis(basis1, basis2):
    """
    Calculate the measurement basis matrix for two qubits.

    Args:
        basis1, basis2: Strings representing the bases ('X', 'Y', 'Z').

    Returns:
        The two-qubit measurement basis matrix as a sympy Matrix.
    """
    R1 = basis_map[basis1]
    R2 = basis_map[basis2]
    return TensorProduct(R1, R2)

# Calculate the measurement basis matrices for all combinations
bases = ['I', 'X', 'Y', 'Z']
measurement_matrices = {}

for b1 in bases:
    for b2 in bases:
        key = f"{b1}{b2}"
        measurement_matrices[key] = two_qubit_measurement_basis(b1, b2)

# Display the measurement basis matrices
for key, matrix in measurement_matrices.items():
    print(f"Measurement basis matrix for {key}:")
    display(matrix)  # Use display to show the matrix visually
    print()

Measurement basis matrix for II:


⎡1  0  0  0⎤
⎢          ⎥
⎢0  1  0  0⎥
⎢          ⎥
⎢0  0  1  0⎥
⎢          ⎥
⎣0  0  0  1⎦


Measurement basis matrix for IX:


⎡0  1  0  0⎤
⎢          ⎥
⎢1  0  0  0⎥
⎢          ⎥
⎢0  0  0  1⎥
⎢          ⎥
⎣0  0  1  0⎦


Measurement basis matrix for IY:


...

⎡0  1  0   0 ⎤
⎢            ⎥
⎢1  0  0   0 ⎥
⎢            ⎥
⎢0  0  0   -1⎥
⎢            ⎥
⎣0  0  -1  0 ⎦


Measurement basis matrix for ZY:


⎡0  -ⅈ  0   0⎤
⎢            ⎥
⎢ⅈ  0   0   0⎥
⎢            ⎥
⎢0  0   0   ⅈ⎥
⎢            ⎥
⎣0  0   -ⅈ  0⎦


Measurement basis matrix for ZZ:


⎡1  0   0   0⎤
⎢            ⎥
⎢0  -1  0   0⎥
⎢            ⎥
⎢0  0   -1  0⎥
⎢            ⎥
⎣0  0   0   1⎦

$$
\textbf{Form 1: Calculation of } \langle \psi | \sigma_i \otimes \sigma_j | \psi \rangle
$$

In [17]:
from sympy import symbols, Matrix, simplify

# Define symbolic coefficients for the two-qubit state
a, b, c, d = symbols('a b c d')

# Define the two-qubit state |psi> as a ket (column vector)
psi_ket = Matrix([[a], [b], [c], [d]])

# Define the conjugate transpose of |psi>, i.e., <psi| as a bra (row vector)
psi_bra = psi_ket.H  # .H gives the conjugate transpose

# Function to calculate <psi| Pauli1 ⊗ Pauli2 |psi>
def expectation_value(psi_ket, psi_bra, pauli_matrix):
    """
    Calculate the expectation value <psi| Pauli1 ⊗ Pauli2 |psi>.
    
    Args:
        psi_ket: The ket vector |psi>.
        psi_bra: The bra vector <psi|.
        pauli_matrix: The two-qubit Pauli matrix (Pauli1 ⊗ Pauli2).
    
    Returns:
        The expectation value as a symbolic expression.
    """
    return simplify(psi_bra * pauli_matrix * psi_ket)[0]  # Simplify and extract scalar result

# Calculate the expectation values for all combinations of Pauli matrices
expectation_values = {}

for key, matrix in measurement_matrices.items():
    expectation_values[key] = expectation_value(psi_ket, psi_bra, matrix)

# Display the expectation values
for key, value in expectation_values.items():
    print(f"<psi| {key} |psi>: {value}")

<psi| II |psi>: a*conjugate(a) + b*conjugate(b) + c*conjugate(c) + d*conjugate(d)
<psi| IX |psi>: a*conjugate(b) + b*conjugate(a) + c*conjugate(d) + d*conjugate(c)
<psi| IY |psi>: I*(a*conjugate(b) - b*conjugate(a) + c*conjugate(d) - d*conjugate(c))
<psi| IZ |psi>: a*conjugate(a) - b*conjugate(b) + c*conjugate(c) - d*conjugate(d)
<psi| XI |psi>: a*conjugate(c) + b*conjugate(d) + c*conjugate(a) + d*conjugate(b)
<psi| XX |psi>: a*conjugate(d) + b*conjugate(c) + c*conjugate(b) + d*conjugate(a)
<psi| XY |psi>: I*(a*conjugate(d) - b*conjugate(c) + c*conjugate(b) - d*conjugate(a))
<psi| XZ |psi>: a*conjugate(c) - b*conjugate(d) + c*conjugate(a) - d*conjugate(b)
<psi| YI |psi>: I*(a*conjugate(c) + b*conjugate(d) - c*conjugate(a) - d*conjugate(b))
<psi| YX |psi>: I*(a*conjugate(d) + b*conjugate(c) - c*conjugate(b) - d*conjugate(a))
<psi| YY |psi>: -a*conjugate(d) + b*conjugate(c) + c*conjugate(b) - d*conjugate(a)
<psi| YZ |psi>: I*(a*conjugate(c) - b*conjugate(d) - c*conjugate(a) + d*conjugate

Two-qubit rotation matrices: 

In [18]:
from sympy import Matrix, eye, I, init_printing
from sympy.physics.quantum import TensorProduct
from IPython.display import display

# Initialize pretty printing for better visualization in Jupyter
init_printing()

# Define Pauli matrices
X = Matrix([[0, 1], [1, 0]])  # Pauli-X
Y = Matrix([[0, -I], [I, 0]])  # Pauli-Y
Z = Matrix([[1, 0], [0, -1]])  # Pauli-Z
H = (1 / 2**0.5) * Matrix([[1, 1], [1, -1]])  # Hadamard
S = Matrix([[1, 0], [0, I]])  # Phase gate

# Define single-qubit rotation matrices
RX = H   # Rotation to X basis
RY = (S * H).H  # Rotation to Y basis
RZ = eye(2)  # Rotation to Z basis (identity)

# Define two-qubit rotation matrices
def two_qubit_rotation(basis1, basis2):
    """
    Calculate the two-qubit rotation matrix for the given bases.
    
    Args:
        basis1, basis2: Strings representing the bases ('X', 'Y', 'Z').
    
    Returns:
        The two-qubit rotation matrix as a sympy Matrix.
    """
    # Map basis to rotation matrices
    basis_map = {'I': RZ, 'X': RX, 'Y': RY, 'Z': RZ}
    R1 = basis_map[basis1]
    R2 = basis_map[basis2]
    return TensorProduct(R1, R2)

# Calculate rotation matrices for all combinations
bases = ['I', 'X', 'Y', 'Z']
rotation_matrices = {}

for b1 in bases:
    for b2 in bases:
        key = f"{b1}{b2}"
        rotation_matrices[key] = two_qubit_rotation(b1, b2)

# Print the rotation matrices
for key, matrix in rotation_matrices.items():
    print(f"Rotation matrix for basis {key}:")
    display(matrix)
    print()

Rotation matrix for basis II:


⎡1  0  0  0⎤
⎢          ⎥
⎢0  1  0  0⎥
⎢          ⎥
⎢0  0  1  0⎥
⎢          ⎥
⎣0  0  0  1⎦


Rotation matrix for basis IX:


⎡0.707106781186547  0.707106781186547           0                  0         ⎤
⎢                                                                            ⎥
⎢0.707106781186547  -0.707106781186547          0                  0         ⎥
⎢                                                                            ⎥
⎢        0                  0           0.707106781186547  0.707106781186547 ⎥
⎢                                                                            ⎥
⎣        0                  0           0.707106781186547  -0.707106781186547⎦


Rotation matrix for basis IY:


...

⎡0.707106781186547  0.707106781186547           0                  0         ⎤
⎢                                                                            ⎥
⎢0.707106781186547  -0.707106781186547          0                  0         ⎥
⎢                                                                            ⎥
⎢        0                  0           0.707106781186547  0.707106781186547 ⎥
⎢                                                                            ⎥
⎣        0                  0           0.707106781186547  -0.707106781186547⎦


Rotation matrix for basis ZY:


⎡0.707106781186547  -0.707106781186547⋅ⅈ          0                   0        ↪
⎢                                                                              ↪
⎢0.707106781186547  0.707106781186547⋅ⅈ           0                   0        ↪
⎢                                                                              ↪
⎢        0                   0            0.707106781186547  -0.70710678118654 ↪
⎢                                                                              ↪
⎣        0                   0            0.707106781186547  0.707106781186547 ↪

↪    ⎤
↪    ⎥
↪    ⎥
↪    ⎥
↪ 7⋅ⅈ⎥
↪    ⎥
↪ ⋅ⅈ ⎦


Rotation matrix for basis ZZ:


⎡1  0  0  0⎤
⎢          ⎥
⎢0  1  0  0⎥
⎢          ⎥
⎢0  0  1  0⎥
⎢          ⎥
⎣0  0  0  1⎦

$$
\textbf{Form 2: Calculation of } \langle \psi' | \sigma_3 \otimes \sigma_3 | \psi' \rangle
$$


(i.e., $<\psi$ |(rotation matrix for a certain basis) ZZ (rotation matrix for a certain basis)| $\psi>$ is calculated)

In [19]:
from sympy import symbols, Matrix, simplify
from sympy.physics.quantum import TensorProduct

# Define symbolic coefficients for the two-qubit state
a, b, c, d = symbols('a b c d')

# Define the two-qubit state |psi> as a ket (column vector)
psi_ket = Matrix([[a], [b], [c], [d]])

# Define the conjugate transpose of |psi>, i.e., <psi| as a bra (row vector)
psi_bra = psi_ket.H  # .H gives the conjugate transpose

# Define the ZZ matrix (Pauli-Z ⊗ Pauli-Z)
Z = Matrix([[1, 0], [0, -1]])  # Pauli-Z
ZZ = TensorProduct(Z, Z)

# Function to calculate <psi | (rotation matrix) ZZ (rotation matrix) | psi>
def calculate_long_expression(psi_ket, psi_bra, rotation_matrix, key):
    """
    Calculate <psi | (rotation matrix) ZZ (rotation matrix) | psi>.
    
    Args:
        psi_ket: The ket vector |psi>.
        psi_bra: The bra vector <psi|.
        rotation_matrix: The two-qubit rotation matrix.
    
    Returns:
        The symbolic result of the calculation.
    """

    key = key.replace('X', 'Z')
    key = key.replace('Y', 'Z')
    matrix = TensorProduct(basis_map[key[0]], basis_map[key[1]])

    rotated_ZZ = rotation_matrix.H * matrix * rotation_matrix  # Apply rotation
    return simplify(psi_bra * rotated_ZZ * psi_ket)[0]  # Simplify and extract scalar result

# Calculate the result for all combinations of rotation matrices
results = {}

for key, rotation_matrix in rotation_matrices.items():
    results[key] = calculate_long_expression(psi_ket, psi_bra, rotation_matrix, key)

# Display the results
for key, value in results.items():
    key2 = key
    key2 = key2.replace('X', 'Z')
    key2 = key2.replace('Y', 'Z')
    formatted_value = simplify(value).evalf()  # Simplify and evaluate numerically
    formatted_value = str(formatted_value).replace("1.0*", "")  # Remove 1.0 coefficients
    print(f"<psi | ({key}) {key2} ({key}) | psi>: {formatted_value}")

<psi | (II) II (II) | psi>: a*conjugate(a) + b*conjugate(b) + c*conjugate(c) + d*conjugate(d)
<psi | (IX) IZ (IX) | psi>: a*conjugate(b) + b*conjugate(a) + c*conjugate(d) + d*conjugate(c)
<psi | (IY) IZ (IY) | psi>: I*(a*conjugate(b) - b*conjugate(a) + c*conjugate(d) - d*conjugate(c))
<psi | (IZ) IZ (IZ) | psi>: a*conjugate(a) - b*conjugate(b) + c*conjugate(c) - d*conjugate(d)
<psi | (XI) ZI (XI) | psi>: a*conjugate(c) + b*conjugate(d) + c*conjugate(a) + d*conjugate(b)
<psi | (XX) ZZ (XX) | psi>: a*conjugate(d) + b*conjugate(c) + c*conjugate(b) + d*conjugate(a)
<psi | (XY) ZZ (XY) | psi>: I*(a*conjugate(d) - b*conjugate(c) + c*conjugate(b) - d*conjugate(a))
<psi | (XZ) ZZ (XZ) | psi>: a*conjugate(c) - b*conjugate(d) + c*conjugate(a) - d*conjugate(b)
<psi | (YI) ZI (YI) | psi>: I*(a*conjugate(c) + b*conjugate(d) - c*conjugate(a) - d*conjugate(b))
<psi | (YX) ZZ (YX) | psi>: I*(a*conjugate(d) + b*conjugate(c) - c*conjugate(b) - d*conjugate(a))
<psi | (YY) ZZ (YY) | psi>: -a*conjugate(d) 

Comparison of Form 1 and Form 2:

In [20]:
# Compare the results from both calculations
comparison_results = {}

for key in measurement_matrices.keys():
    # Get the results from both methods
    result_long = results[key]  # From calculate_long_expression
    result_direct = expectation_values[key]  # From expectation_value
    
    # Check if they are equal
    comparison_results[key] = simplify(result_long - result_direct) == 0
    print(simplify(result_long - result_direct))

0
-2.22044604925031e-16*a*conjugate(b) - 2.22044604925031e-16*b*conjugate(a) - 2.22044604925031e-16*c*conjugate(d) - 2.22044604925031e-16*d*conjugate(c)
2.22044604925031e-16*I*(-a*conjugate(b) + b*conjugate(a) - c*conjugate(d) + d*conjugate(c))
0
-2.22044604925031e-16*a*conjugate(c) - 2.22044604925031e-16*b*conjugate(d) - 2.22044604925031e-16*c*conjugate(a) - 2.22044604925031e-16*d*conjugate(b)
-4.44089209850063e-16*a*conjugate(d) - 4.44089209850063e-16*b*conjugate(c) - 4.44089209850063e-16*c*conjugate(b) - 4.44089209850063e-16*d*conjugate(a)
4.44089209850063e-16*I*(-a*conjugate(d) + b*conjugate(c) - c*conjugate(b) + d*conjugate(a))
-2.22044604925031e-16*a*conjugate(c) + 2.22044604925031e-16*b*conjugate(d) - 2.22044604925031e-16*c*conjugate(a) + 2.22044604925031e-16*d*conjugate(b)
2.22044604925031e-16*I*(-a*conjugate(c) - b*conjugate(d) + c*conjugate(a) + d*conjugate(b))
4.44089209850063e-16*I*(-a*conjugate(d) - b*conjugate(c) + c*conjugate(b) + d*conjugate(a))
4.44089209850063e-16*a*c

Given that the numbers are practically 0, both forms are equal.


Finally, verify that the density matrix (ρ) reconstructed from experimental expectation values matches the theoretical density matrix (|ψ⟩⟨ψ|) computed directly from the quantum state:

In [21]:
from sympy import Matrix, symbols, simplify
from sympy.physics.quantum import TensorProduct

# Define symbolic coefficients for the two-qubit state
a, b, c, d = symbols('a b c d')

# Define the two-qubit state |psi> as a ket (column vector)
psi_ket = Matrix([[a], [b], [c], [d]])

# Define the conjugate transpose of |psi>, i.e., <psi| as a bra (row vector)
psi_bra = psi_ket.H  # .H gives the conjugate transpose

# Calculate |psi><psi| directly
rho_direct = psi_ket * psi_bra

# Define Pauli matrices
I = Matrix([[1, 0], [0, 1]])  # Identity
X = Matrix([[0, 1], [1, 0]])  # Pauli-X
Y = Matrix([[0, -1j], [1j, 0]])  # Pauli-Y
Z = Matrix([[1, 0], [0, -1]])  # Pauli-Z

# List of Pauli matrices
pauli_matrices = [I, X, Y, Z]
pauli_matrices_names = ['I', 'X', 'Y', 'Z']

# Construct rho from expectation values
rho_from_expectations = Matrix.zeros(4, 4)  # Initialize a 4x4 zero matrix

# SHORT EXPECTATION VALUES

# Iterate over all combinations of Pauli matrices
for i, sigma_i in enumerate(pauli_matrices):
    for j, sigma_j in enumerate(pauli_matrices):
        # Calculate the Kronecker product sigma_i ⊗ sigma_j
        sigma_ij = TensorProduct(sigma_i, sigma_j)
        
        # Get the expectation value <psi| sigma_i ⊗ sigma_j |psi>
        expectation_value = expectation_values[pauli_matrices_names[i]+pauli_matrices_names[j]] #simplify(psi_bra * sigma_ij * psi_ket)[0]
        
        # Add the contribution to rho
        rho_from_expectations += (1 / 4) * expectation_value * sigma_ij

# Compare the two matrices
are_equal = simplify(rho_direct - rho_from_expectations) == Matrix.zeros(4, 4)

# Display the results
print("Directly calculated rho (|psi><psi|):")
display(rho_direct)

print("\nRho constructed from expectation values (Form 1):")
display(rho_from_expectations)

print("\nAre the two matrices equal?")
print(are_equal)

# LONG EXPECTATION VALUES

rho_from_expectations = Matrix.zeros(4, 4)

# Iterate over all combinations of Pauli matrices
for i, sigma_i in enumerate(pauli_matrices):
    for j, sigma_j in enumerate(pauli_matrices):
        # Calculate the Kronecker product sigma_i ⊗ sigma_j
        sigma_ij = TensorProduct(sigma_i, sigma_j)
        
        # Get the expectation value <psi| sigma_i ⊗ sigma_j |psi>
        expectation_value = results[pauli_matrices_names[i]+pauli_matrices_names[j]] #simplify(psi_bra * sigma_ij * psi_ket)[0]
        
        # Add the contribution to rho
        rho_from_expectations += (1 / 4) * expectation_value * sigma_ij

# Compare the two matrices


# Display the results

print("\nRho constructed with measurements in Z basis (Form 2):")
display(rho_from_expectations)

print("\nAre the two matrices equal?")
display(simplify(rho_direct - rho_from_expectations))

Directly calculated rho (|psi><psi|):


⎡  _    _    _    _⎤
⎢a⋅a  a⋅b  a⋅c  a⋅d⎥
⎢                  ⎥
⎢  _    _    _    _⎥
⎢b⋅a  b⋅b  b⋅c  b⋅d⎥
⎢                  ⎥
⎢  _    _    _    _⎥
⎢c⋅a  c⋅b  c⋅c  c⋅d⎥
⎢                  ⎥
⎢  _    _    _    _⎥
⎣d⋅a  d⋅b  d⋅c  d⋅d⎦


Rho constructed from expectation values (Form 1):


⎡      _        _        _        _⎤
⎢1.0⋅a⋅a  1.0⋅a⋅b  1.0⋅a⋅c  1.0⋅a⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎢1.0⋅b⋅a  1.0⋅b⋅b  1.0⋅b⋅c  1.0⋅b⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎢1.0⋅c⋅a  1.0⋅c⋅b  1.0⋅c⋅c  1.0⋅c⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎣1.0⋅d⋅a  1.0⋅d⋅b  1.0⋅d⋅c  1.0⋅d⋅d⎦


Are the two matrices equal?
True

Rho constructed with measurements in Z basis (Form 2):


⎡      _        _        _        _⎤
⎢1.0⋅a⋅a  1.0⋅a⋅b  1.0⋅a⋅c  1.0⋅a⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎢1.0⋅b⋅a  1.0⋅b⋅b  1.0⋅b⋅c  1.0⋅b⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎢1.0⋅c⋅a  1.0⋅c⋅b  1.0⋅c⋅c  1.0⋅c⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎣1.0⋅d⋅a  1.0⋅d⋅b  1.0⋅d⋅c  1.0⋅d⋅d⎦


Are the two matrices equal?


⎡                                                 _                         _  ↪
⎢           0              2.22044604925031e-16⋅a⋅b  2.22044604925031e-16⋅a⋅c  ↪
⎢                                                                              ↪
⎢                       _                                                   _  ↪
⎢2.22044604925031e-16⋅b⋅a             0              4.44089209850063e-16⋅b⋅c  ↪
⎢                                                                              ↪
⎢                       _                         _                            ↪
⎢2.22044604925031e-16⋅c⋅a  4.44089209850063e-16⋅c⋅b             0              ↪
⎢                                                                              ↪
⎢                       _                         _                         _  ↪
⎣4.44089209850063e-16⋅d⋅a  2.22044604925031e-16⋅d⋅b  2.22044604925031e-16⋅d⋅c  ↪

↪                         _⎤
↪  4.44089209850063e-16⋅a⋅d⎥
↪                          ⎥
↪                    

Comparison between the benchmarking 1 (linear inversion algorithm) and benchmarking 2.

In [22]:
initial_state

array([ 0.09151495-0.15968985j, -0.70360438+0.28319234j,
       -0.30551389-0.14560187j,  0.05456838-0.5228296j ])

In [23]:
from sympy import Symbol
a = Symbol('a')
b = Symbol('b')
c = Symbol('c')
d = Symbol('d')

In [24]:
simplify(rho_from_expectations.subs({a:initial_state[0], b:initial_state[1], c:initial_state[2], d:initial_state[3]}))

⎡            0.0338758336049558              -0.109613260639397 + 0.0864421443 ↪
⎢                                                                              ↪
⎢-0.109613260639397 - 0.0864421443800404⋅ⅈ               0.575257024233621     ↪
⎢                                                                              ↪
⎢-0.0047079481153484 - 0.0621122140256894⋅ⅈ   0.173727577748997 + 0.1889653033 ↪
⎢                                                                              ↪
⎣0.0884844028615789 - 0.0391327077149655⋅ⅈ    -0.1864558911455 + 0.35241185079 ↪

↪ 800404⋅ⅈ  -0.0047079481153484 + 0.0621122140256894⋅ⅈ  0.0884844028615789 + 0 ↪
↪                                                                              ↪
↪            0.173727577748997 - 0.188965303372808⋅ⅈ     -0.1864558911455 - 0. ↪
↪                                                                              ↪
↪ 72808⋅ⅈ               0.114538639901166               0.0594535668935435 - 0 ↪
↪                          

In [25]:
display(Matrix(ideal_rho))

⎡            0.0338758336049558              -0.109613260639397 + 0.0864421443 ↪
⎢                                                                              ↪
⎢-0.109613260639397 - 0.0864421443800404⋅ⅈ               0.575257024233621     ↪
⎢                                                                              ↪
⎢-0.0047079481153484 - 0.0621122140256894⋅ⅈ   0.173727577748997 + 0.1889653033 ↪
⎢                                                                              ↪
⎣0.0884844028615789 - 0.0391327077149656⋅ⅈ    -0.1864558911455 + 0.35241185079 ↪

↪ 800404⋅ⅈ  -0.0047079481153484 + 0.0621122140256894⋅ⅈ  0.0884844028615789 + 0 ↪
↪                                                                              ↪
↪            0.173727577748997 - 0.188965303372808⋅ⅈ     -0.1864558911455 - 0. ↪
↪                                                                              ↪
↪ 72808⋅ⅈ               0.114538639901166               0.0594535668935435 - 0 ↪
↪                          

In [26]:
rho_direct

⎡  _    _    _    _⎤
⎢a⋅a  a⋅b  a⋅c  a⋅d⎥
⎢                  ⎥
⎢  _    _    _    _⎥
⎢b⋅a  b⋅b  b⋅c  b⋅d⎥
⎢                  ⎥
⎢  _    _    _    _⎥
⎢c⋅a  c⋅b  c⋅c  c⋅d⎥
⎢                  ⎥
⎢  _    _    _    _⎥
⎣d⋅a  d⋅b  d⋅c  d⋅d⎦

In [27]:
rho_from_expectations

⎡      _        _        _        _⎤
⎢1.0⋅a⋅a  1.0⋅a⋅b  1.0⋅a⋅c  1.0⋅a⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎢1.0⋅b⋅a  1.0⋅b⋅b  1.0⋅b⋅c  1.0⋅b⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎢1.0⋅c⋅a  1.0⋅c⋅b  1.0⋅c⋅c  1.0⋅c⋅d⎥
⎢                                  ⎥
⎢      _        _        _        _⎥
⎣1.0⋅d⋅a  1.0⋅d⋅b  1.0⋅d⋅c  1.0⋅d⋅d⎦